# Download Dataset and Augumented Dataset

In [ ]:
!pip install pytorch-lightning


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 815.2/815.2 kB 10.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 866.2/866.2 kB 32.0 MB/s eta 0:00:00


In [ ]:
!pip install sentence-transformers


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 227.1/227.1 kB 1.5 MB/s eta 0:00:00


In [ ]:
!mkdir collections/msmarco-passage

!wget https://msmarco.z22.web.core.windows.net/msmarcoranking/collectionandqueries.tar.gz -P collections/msmarco-passage

# Alternative mirror:
# wget https://rgw.cs.uwaterloo.ca/JIMMYLIN-bucket0/data/collectionandqueries.tar.gz -P collections/msmarco-passage

!tar xvfz collections/msmarco-passage/collectionandqueries.tar.gz -C collections/msmarco-passage

mkdir: cannot create directory ‘collections/msmarco-passage’: No such file or directory
--2024-08-29 18:22:04--  https://msmarco.z22.web.core.windows.net/msmarcoranking/collectionandqueries.tar.gz
Resolving msmarco.z22.web.core.windows.net (msmarco.z22.web.core.windows.net)... 20.150.34.1
Connecting to msmarco.z22.web.core.windows.net (msmarco.z22.web.core.windows.net)|20.150.34.1|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 1057717952 (1009M) [application/gzip]
Saving to: ‘collections/msmarco-passage/collectionandqueries.tar.gz’

collectionandquerie 100%[===================>]   1009M  83.5MB/s    in 11s     

2024-08-29 18:22:15 (92.8 MB/s) - ‘collections/msmarco-passage/collectionandqueries.tar.gz’ saved [1057717952/1057717952]

collection.tsv
qrels.dev.small.tsv
qrels.train.tsv
queries.dev.small.tsv
queries.dev.tsv
queries.eval.small.tsv
queries.eval.tsv
queries.train.tsv


In [ ]:
!gdown  https://drive.google.com/uc?id=1mW8IScwTTCALFJNZ0Ca5z3AGO0bjCQB3

!unzip DSI_Dataset.zip -d collections/msmarco-passage


Downloading...
From: https://drive.google.com/uc?id=1mW8IScwTTCALFJNZ0Ca5z3AGO0bjCQB3
To: /content/DSI_Dataset.zip
100% 17.5M/17.5M [00:00<00:00, 22.3MB/s]
Archive:  DSI_Dataset.zip
  inflating: collections/msmarco-passage/eval_data_with_passages_ids.json  
  inflating: collections/msmarco-passage/test_data_with_passages_ids.json  
  inflating: collections/msmarco-passage/train_data_with_passages_ids.json  


In [ ]:
!gdown  https://drive.google.com/uc?id=1O_nIekrR3Lzbfa0a6MhB5Vp-atUF7HHK
!unzip weights_model.zip

Downloading...
From (original): https://drive.google.com/uc?id=1O_nIekrR3Lzbfa0a6MhB5Vp-atUF7HHK
From (redirected): https://drive.google.com/uc?id=1O_nIekrR3Lzbfa0a6MhB5Vp-atUF7HHK&confirm=t&uuid=8f0495fd-6d68-4f32-8548-5007858afd30
To: /content/weights_model.zip
100% 387M/387M [00:12<00:00, 32.1MB/s]
Archive:  weights_model.zip
  inflating: cluster_predictor_weights.pth  
  inflating: combined_model.pth      


# Augument Dataset
We dont need anymore this section since the results are saved in google drive and downloaded previously

In [ ]:
import pandas as pd
from transformers import T5ForConditionalGeneration, T5Tokenizer
from sklearn.cluster import KMeans
import torch
from tqdm import tqdm
import json
from sentence_transformers import SentenceTransformer

# Split into training and test sets
train_size = 80000
test_size = 20000  # this will be test_size = test_size - eval_size = 18k since we extract eval set from test set
eval_size = 2000

# Define the paths to the files
passages_file_path = 'collections/msmarco-passage/collection.tsv'
queries_file_path = 'collections/msmarco-passage/queries.train.tsv'
qrels_file_path = 'collections/msmarco-passage/qrels.train.tsv'

# Load the data
passages_df = pd.read_csv(passages_file_path, sep='\t', header=None, names=[
                          'doc_id', 'passage_text'])
queries_df = pd.read_csv(queries_file_path, sep='\t',
                         header=None, names=['query_id', 'query_text'])
qrels_df = pd.read_csv(qrels_file_path, sep='\t', header=None, names=[
                       'query_id', 'Q0', 'doc_id', 'relevance'])

# Combine qrels with queries and passages to get the full dataset
full_dataset = qrels_df[['query_id', 'doc_id']].merge(
    queries_df, on='query_id').merge(passages_df, on='doc_id')

# Shuffle the dataset
full_dataset = full_dataset.sample(
    frac=1, random_state=42).reset_index(drop=True)

train_dataset = full_dataset.iloc[:train_size].copy()
del full_dataset

# Encode passages using SentenceTransformer
sentence_model = SentenceTransformer('all-MiniLM-L6-v2') #.to('cuda')
# Function to generate embeddings with batching
def generate_embeddings(texts, batch_size=512):
    embeddings = []
    for i in tqdm(range(0, len(texts), batch_size), desc="Generating Embeddings"):
        batch_texts = texts[i:i + batch_size]
        batch_embeddings = sentence_model.encode(
            batch_texts, show_progress_bar=False)
        embeddings.extend(batch_embeddings)
    return embeddings


# Generate embeddings for the training dataset
embeddings = generate_embeddings(train_dataset['passage_text'].tolist())
del sentence_model
# Cluster the training dataset into 2k clusters
kmeans = KMeans(n_clusters=2000, random_state=42)
train_dataset['cluster_id'] = kmeans.fit_predict(embeddings)


test_dataset = train_dataset.sample(n=test_size, random_state=42)


KeyboardInterrupt: 

In [ ]:
# Save some memory...
import gc
del passages_df
del queries_df
del qrels_df
del embeddings
del kmeans
gc.collect()  # garbage collection
torch.cuda.empty_cache()
gc.collect()  # garbage collection


NameError: name 'passages_df' is not defined

In [ ]:
from transformers import T5ForConditionalGeneration, T5Tokenizer
# Initialize the T5 model and tokenizer
model_name = 'doc2query/all-t5-base-v1'
model = T5ForConditionalGeneration.from_pretrained(model_name).to('cuda')
tokenizer = T5Tokenizer.from_pretrained(model_name)

# Generate pseudo-queries for the test set


def generate_pseudo_queries(documents, batch_size=128):
    pseudo_queries = []
    for i in tqdm(range(0, len(documents), batch_size), desc="Generating Pseudo-Queries"):
        batch_docs = documents[i:i+batch_size]
        input_texts = [
            f"generate query: {doc['passage_text']}" for doc in batch_docs]
        input_ids = tokenizer(input_texts, return_tensors='pt',
                              padding=True, truncation=True, max_length=512)
        outputs = model.generate(input_ids['input_ids'].to(
            'cuda'), max_length=64, num_return_sequences=1)
        batch_pseudo_queries = [tokenizer.decode(
            output, skip_special_tokens=True) for output in outputs]
        pseudo_queries.extend(batch_pseudo_queries)
    return pseudo_queries


test_docs = test_dataset.to_dict(orient='records')
pseudo_queries = generate_pseudo_queries(test_docs)
del model
del tokenizer
gc.collect()  # garbage collection
torch.cuda.empty_cache()
gc.collect()  # garbage collection
# Add pseudo queries to test dataset
test_dataset['pseudo_query_text'] = pseudo_queries

# Create the required data structures
train_data = train_dataset[['query_id', 'query_text',
                            'doc_id', 'cluster_id']].to_dict(orient='records')
test_data = test_dataset[['query_id', 'pseudo_query_text',
                          'doc_id', 'cluster_id']].to_dict(orient='records')

# Save the datasets to JSON files for easy loading
with open('collections/msmarco-passage/train_data.json', 'w') as f:
    json.dump(train_data, f)

with open('collections/msmarco-passage/test_data.json', 'w') as f:
    json.dump(test_data, f)

print(f"Training data saved to collections/msmarco-passage/train_data.json")
print(f"test data saved to collections/msmarco-passage/test_data.json")


Generating Pseudo-Queries: 100%|██████████| 157/157 [10:04<00:00,  3.85s/it]


Training data saved to collections/msmarco-passage/train_data.json
Evaluation data saved to collections/msmarco-passage/eval_data.json


For simplicity, lets add to the dataset train_data and eval_data the passage_text also to the json file (so the correspondaces between query_id and passage_text)

In [ ]:

# Define the paths to the files
train_data_path = 'collections/msmarco-passage/train_data.json'
test_data_path = 'collections/msmarco-passage/eval_data.json'


# Create a mapping from doc_id to passage_text
doc_text_mapping = pd.Series(
    passages_df.passage_text.values, index=passages_df.doc_id).to_dict()

# Function to add passage text to the data


def add_passage_text(data, mapping):
    for item in data:
        doc_id = item['doc_id']
        item['passage_text'] = mapping.get(doc_id, "Document not found")
    return data


# Load the JSON files
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(test_data_path, 'r') as f:
    test_data = json.load(f)

# Add passage text to train and test data
train_data = add_passage_text(train_data, doc_text_mapping)
test_data = add_passage_text(test_data, doc_text_mapping)

# Save the updated JSON files
with open('collections/msmarco-passage/train_data_with_passages.json', 'w') as f:
    json.dump(train_data, f)

with open('collections/msmarco-passage/test_data_with_passages.json', 'w') as f:
    json.dump(test_data, f)

print(f"Updated training data saved to collections/msmarco-passage/train_data_with_passages.json")
print(f"Updated test data saved to collections/msmarco-passage/test_data_with_passages.json")


Last but not least, change all id_query such that they start form 1 and finish to 80k. And lets create also eval dataset, by  extracting 2k samples from the test set

In [ ]:
import json
import pandas as pd

# Paths to the datasets
train_data_path = 'collections/msmarco-passage/train_data_with_passages_ids.json'
test_data_path = 'collections/msmarco-passage/test_data_with_passages_ids.json'

# Load the datasets
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(test_data_path, 'r') as f:
    test_data = json.load(f)

# Update query_ids for train_data
for i, item in enumerate(train_data):
    item['query_id'] = i + 1

# Update query_ids for test_data starting from the last query_id of train_data
start_test_query_id = len(train_data) + 1
for i, item in enumerate(test_data):
    item['query_id'] = start_test_query_id + i

# Convert test_data to DataFrame to easily manipulate rows
test_df = pd.DataFrame(test_data)

# Extract a sample for evaluation from the test dataset
eval_df = test_df.sample(n=eval_size, random_state=42)

# Remove evaluation samples from the test dataset
remaining_test_df = test_df.drop(eval_df.index)

# Convert back to list of dicts
eval_data = eval_df.to_dict(orient='records')
test_data = remaining_test_df.to_dict(orient='records')

# Save the updated datasets
updated_train_data_path = 'collections/msmarco-passage/train_data_with_passages_ids.json'
updated_test_data_path = 'collections/msmarco-passage/test_data_with_passages_ids.json'
eval_data_path = 'collections/msmarco-passage/eval_data_with_passages_ids.json'

with open(updated_train_data_path, 'w') as f:
    json.dump(train_data, f)

with open(updated_test_data_path, 'w') as f:
    json.dump(test_data, f)

with open(eval_data_path, 'w') as f:
    json.dump(eval_data, f)

# Verify no common query_ids between train_data and eval_data
train_query_ids = set(item['query_id'] for item in train_data)
test_query_ids = set(item['query_id'] for item in test_data)
eval_query_ids = set(item['query_id'] for item in eval_data)

common_query_ids_train_test = train_query_ids & test_query_ids
common_query_ids_train_eval = train_query_ids & eval_query_ids
common_query_ids_test_eval = test_query_ids & eval_query_ids

if common_query_ids_train_test:
    print("Found common query_ids between train_data and test_data:",
          common_query_ids_train_test)
else:
    print("No common query_ids between train_data and test_data.")

if common_query_ids_train_eval:
    print("Found common query_ids between train_data and eval_data:",
          common_query_ids_train_eval)
else:
    print("No common query_ids between train_data and eval_data.")

if common_query_ids_test_eval:
    print("Found common query_ids between test_data and eval_data:",
          common_query_ids_test_eval)
else:
    print("No common query_ids between test_data and eval_data.")


No common query_ids between train_data and test_data.
No common query_ids between train_data and eval_data.
No common query_ids between test_data and eval_data.


## Small check of the dataset. comparing query text and pseudo query text

In [ ]:
import json

# Paths to the JSON files
train_data_path = 'collections/msmarco-passage/train_data.json'
eval_data_path = 'collections/msmarco-passage/eval_data.json'

# Load the JSON files
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(eval_data_path, 'r') as f:
    eval_data = json.load(f)

# Create a mapping from query_id to pseudo_query_text using the eval_data
pseudo_query_mapping = {item['query_id']                        : item['pseudo_query_text'] for item in eval_data}

# Create a mapping from query_id to query_text using the train_data
query_text_mapping = {item['query_id']: item['query_text']
                      for item in train_data}

# Find all query_id correspondences between train and eval
common_query_ids = set(query_text_mapping.keys()) & set(
    pseudo_query_mapping.keys())

# Combine data to find the corresponding pseudo query text for each query text in the train_data
query_pseudo_query_pairs = []
for query_id in common_query_ids:
    query_text = query_text_mapping[query_id]
    pseudo_query_text = pseudo_query_mapping[query_id]
    query_pseudo_query_pairs.append((query_text, pseudo_query_text))

# Print the results
for query_text, pseudo_query_text in query_pseudo_query_pairs:
    print(
        f"Query Text: {query_text}\nPseudo Query Text: {pseudo_query_text}\n")


# BM25 Baseline
I decided to build it in a customized manner. The problem of using the pre-built indexes is that it considers the entire collection.tsv, which includes more passages than necessary. For instance, when using queries.train.tsv, the SimpleSearcher function considers the entire collection.tsv. However, I want to index only the passages that are directly linked to the queries + the passages that i considered. This approach ensures that only the relevant passages associated with the corresponding queries are indexed, excluding any passage that does not have an associated query ( so we dont cosinder the entire collection.tsv) . in fact, later when we create our model, we will consider only passages that has its corresponding query. Also, is important to do it to create a fair and efficient index for comparison (in evaluation) with our model, since also in our model we will not be using the entire collection.tsv for computational reasons.

## Dataset Analysis


In [ ]:
import pandas as pd

# Define the paths to the files
# or queries.dev.small.tsv
queries_file_path = 'collections/msmarco-passage/queries.dev.small.tsv'
passages_file_path = 'collections/msmarco-passage/collection.tsv'
# or qrels.dev.small.tsv
qrels_file_path = 'collections/msmarco-passage/qrels.dev.small.tsv'


# Read the queries file into a pandas DataFrame
queries_df = pd.read_csv(queries_file_path, sep='\t', header=None, names=[
                         'query_id', 'query_text'], nrows=100000)

# Read the qrels file into a pandas DataFrame to get the required doc_ids
qrels_df = pd.read_csv(qrels_file_path, sep='\t', header=None, names=[
                       'query_id', 'Q0', 'doc_id', 'relevance'])


# Filter the qrels to include only the first 100k queries
qrels_df = qrels_df[qrels_df['query_id'].isin(queries_df['query_id'])]

# Get unique doc_ids from the filtered qrels
required_doc_ids = qrels_df['doc_id'].unique()

# Read the passages file and filter it to include only the required doc_ids
passages_df = pd.read_csv(passages_file_path, sep='\t', header=None, names=[
                          'doc_id', 'passage_text'])
filtered_passages_df = passages_df[passages_df['doc_id'].isin(
    required_doc_ids)]

# Verify the shapes of the DataFrames
print(f"queries_df shape: {queries_df.shape}")
print(f"qrels_df shape: {qrels_df.shape}")
print(f"filtered_passages_df shape: {filtered_passages_df.shape}")

# Create dictionaries to map IDs to texts
query_dict = pd.Series(
    queries_df['query_text'].values, index=queries_df['query_id']).to_dict()
passage_dict = pd.Series(
    filtered_passages_df['passage_text'].values, index=filtered_passages_df['doc_id']).to_dict()

print(f"Number of queries: {len(query_dict)}")
print(f"Number of passages: {len(passage_dict)}")

# Function to get query and passage text given query_id and doc_id


def get_query_and_passage(query_id, doc_id):
    query_text = query_dict.get(query_id, "Query not found")
    passage_text = passage_dict.get(doc_id, "Passage not found")
    return query_text, passage_text


queries_df shape: (6980, 2)
qrels_df shape: (7437, 4)
filtered_passages_df shape: (7433, 2)
Number of queries: 6980
Number of passages: 7433


In [ ]:
import pandas as pd

# Load the first CSV file
queries_df1 = pd.read_csv('collections/msmarco-passage/qrels.dev.small.tsv',
                          sep='\t', header=None, names=['query_id', 'Q0', 'doc_id', 'relevance'])

# Load the second CSV file
queries_df2 = pd.read_csv('collections/msmarco-passage/qrels.train.tsv',
                          sep='\t', header=None, names=['query_id', 'Q0', 'doc_id', 'relevance'])

# Extract the 'query_id' columns
query_ids_1 = set(queries_df1['doc_id'])
query_ids_2 = set(queries_df2['doc_id'])

# Find the query_ids in queries_df1 that are not in queries_df2
missing_query_ids = query_ids_1 - query_ids_2

# Count the number of missing query_ids
num_missing_query_ids = len(missing_query_ids)

# Display the number of missing query_ids
print(
    f'The number of query_ids in queries_df1 that are not in queries_df2 is: {num_missing_query_ids}')
print(len(query_ids_1))
print(len(query_ids_2))


The number of query_ids in queries_df1 that are not in queries_df2 is: 7126
7433
516472


In [ ]:
import pandas as pd

# Load the training qrels file
train_qrels_path = 'collections/msmarco-passage/qrels.train.tsv'
train_qrels_df = pd.read_csv(train_qrels_path, sep='\t', header=None, names=[
                             'query_id', 'Q0', 'doc_id', 'relevance'])

# Get unique document IDs from the training set
train_doc_ids = train_qrels_df['doc_id'].unique()


In [ ]:
# Load the evaluation qrels file
dev_qrels_path = 'collections/msmarco-passage/qrels.dev.small.tsv'
dev_qrels_df = pd.read_csv(dev_qrels_path, sep='\t', header=None, names=[
                           'query_id', 'Q0', 'doc_id', 'relevance'])

# Filter the evaluation set to include only document IDs present in the training set
filtered_dev_qrels_df = dev_qrels_df[dev_qrels_df['doc_id'].isin(
    train_doc_ids)]

# Save the filtered evaluation qrels to a new file
filtered_dev_qrels_path = 'collections/msmarco-passage/filtered_qrels.dev.small.tsv'
filtered_dev_qrels_df.to_csv(
    filtered_dev_qrels_path, sep='\t', header=False, index=False)

# Verify the number of common document IDs
num_common_doc_ids = len(filtered_dev_qrels_df['doc_id'].unique())
print(
    f'The number of common document IDs in the filtered evaluation dataset is: {num_common_doc_ids}')


The number of common document IDs in the filtered evaluation dataset is: 307


In [ ]:
import pandas as pd

# Load the training qrels file
train_qrels_path = 'collections/msmarco-passage/qrels.train.tsv'
train_qrels_df = pd.read_csv(train_qrels_path, sep='\t', header=None, names=[
                             'query_id', 'Q0', 'doc_id', 'relevance'])

# Load the evaluation qrels file
dev_qrels_path = 'collections/msmarco-passage/qrels.dev.small.tsv'
dev_qrels_df = pd.read_csv(dev_qrels_path, sep='\t', header=None, names=[
                           'query_id', 'Q0', 'doc_id', 'relevance'])

# Identify document IDs present in the training dataset
train_doc_ids = train_qrels_df['doc_id'].unique()

# Filter the evaluation dataset to include only document IDs present in the training dataset
filtered_dev_qrels_df = dev_qrels_df[dev_qrels_df['doc_id'].isin(
    train_doc_ids)]

# Save the filtered evaluation qrels to a new file
filtered_dev_qrels_path = 'collections/msmarco-passage/filtered_qrels.dev.small.tsv'
filtered_dev_qrels_df.to_csv(
    filtered_dev_qrels_path, sep='\t', header=False, index=False)

# Verify the number of common document IDs
num_common_doc_ids = len(filtered_dev_qrels_df['doc_id'].unique())
print(
    f'The number of common document IDs in the filtered evaluation dataset is: {num_common_doc_ids}')


The number of common document IDs in the filtered evaluation dataset is: 307


In [ ]:
# Display the first few objects to verify
print("Iterating through qrels_df:")
for index, row in qrels_df.iterrows():

    print(
        f"Row {index}: Query ID {row['query_id']}, Document ID {row['doc_id']}")
    query_text, passage_text = get_query_and_passage(
        row['query_id'], row['doc_id'])
    print(f"Query ID: {row['query_id']}, Document ID: {row['doc_id']}")
    print(f"Query Text: {query_text}")
    print(f"Passage Text: {passage_text}\n")
    break


Iterating through qrels_df:
Row 0: Query ID 300674, Document ID 7067032
Query ID: 300674, Document ID: 7067032
Query Text: how many years did william bradford serve as governor of plymouth colony?
Passage Text: http://en.wikipedia.org/wiki/William_Bradford_(Plymouth_Colony_governor) William Bradford (c.1590 â 1657) was an English Separatist leader in Leiden, Holland and in Plymouth Colony was a signatory to the Mayflower Compact. He served as Plymouth Colony Governor five times covering about thirty years between 1621 and 1657.



In [ ]:
# Group by query_id and count the number of doc_id for each query_id
query_doc_counts = qrels_df.groupby('query_id')['doc_id'].count()

# Filter query_ids that have more than one doc_id
multiple_passages_query_ids = query_doc_counts[query_doc_counts > 1].index.tolist(
)

# Display the results
print(
    f"Number of query_ids with multiple passage_ids: {len(multiple_passages_query_ids)}")
# Display first 10 as example
print(f"Query IDs with multiple passages: {multiple_passages_query_ids[:10]}")


Number of query_ids with multiple passage_ids: 390
Query IDs with multiple passages: [2962, 4947, 13397, 19940, 27743, 31432, 34015, 43781, 45924, 47588]


In [ ]:
# Example of a question having multiple documents related to it
example_query_id = 300674

# Find all doc_ids associated with the example query_id
related_doc_ids = qrels_df[qrels_df['query_id']
                           == example_query_id]['doc_id'].tolist()

# Print query and passages for the given query_id and multiple doc_ids
print(
    f"Query ID: {example_query_id}\nQuery Text: {query_dict[example_query_id]}")
for doc_id in related_doc_ids:
    query_text, passage_text = get_query_and_passage(example_query_id, doc_id)
    print(f"\nDoc ID: {doc_id}\nPassage Text: {passage_text}")


Query ID: 300674
Query Text: how many years did william bradford serve as governor of plymouth colony?

Doc ID: 7067032
Passage Text: http://en.wikipedia.org/wiki/William_Bradford_(Plymouth_Colony_governor) William Bradford (c.1590 â 1657) was an English Separatist leader in Leiden, Holland and in Plymouth Colony was a signatory to the Mayflower Compact. He served as Plymouth Colony Governor five times covering about thirty years between 1621 and 1657.


## Dataset verification correctness

We are just making sure that the dataset is correct, meaning that for each query i have the corresponding document




In [ ]:
# Ensure each query_id in qrels has a corresponding passage
aligned_query_passages = qrels_df[qrels_df['doc_id'].isin(passage_dict.keys())]
aligned_query_ids = aligned_query_passages['query_id'].unique()

# Create a new query dictionary with only aligned queries
aligned_query_dict = {qid: query_dict[qid] for qid in aligned_query_ids}

# Display the length of each aligned dictionary
print(f"Number of aligned passages: {len(passage_dict)}")
print(f"Number of aligned queries: {len(aligned_query_dict)}")


Number of aligned passages: 7433
Number of aligned queries: 6980


In [ ]:
# Check for missing passages for any query
missing_passages = [
    qid for qid in aligned_query_ids if qid not in aligned_query_dict]
print(
    f"Number of queries without corresponding passages: {len(missing_passages)}")

# Verify if any passages are missing for queries in qrels
missing_query_passages = aligned_query_passages[~aligned_query_passages['query_id'].isin(
    aligned_query_dict.keys())]
print(f"Number of missing query passages: {len(missing_query_passages)}")


Number of queries without corresponding passages: 0
Number of missing query passages: 0


## Installation Pyserini


Install Python dependencies:


In [ ]:
%%capture
!pip install pyserini==0.12.0

import os
os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-11-openjdk-amd64"

First, we need to convert train_data.json and eval_data.json to JSONL format, as required by Pyserini.

In [ ]:
import json
import os

# Paths to the JSON files
train_data_path = 'collections/msmarco-passage/train_data_with_passages_ids.json'
test_data_path = 'collections/msmarco-passage/test_data_with_passages_ids.json'

# Directory to save the JSON files
output_dir = "json_collection"
os.makedirs(output_dir, exist_ok=True)

# Convert train_data.json to JSONL for indexing
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(os.path.join(output_dir, 'train_data_for_indexing.jsonl'), 'w') as outfile:
    for item in train_data:
        json_record = {
            'id': item['doc_id'],
            'contents': item['passage_text']
        }
        outfile.write(json.dumps(json_record) + '\n')


In [ ]:
train_data[1]


{'query_id': 2,
 'query_text': 'why do they use a yag laser in eyes?',
 'doc_id': 3351843,
 'cluster_id': 1778,
 'passage_text': 'In podiatry, the Nd:YAG laser is being used to treat onychomycosis, which is fungus infection of the toenail. The merits of laser treatment of these infections are not yet clear, and research is being done to establish effectiveness.'}

In [ ]:
# OPPURE, generare json usando pyserini. prima convertire in tsv filtered_collection

#!cd anserini && python ./src/main/python/msmarco/convert_collection_to_jsonl.py \
# --collection_path ../data/msmarco_passage/collection.tsv --output_folder ../data/msmarco_passage/collection_jsonl


Generate the index

In [ ]:
!python -m pyserini.index -collection JsonCollection -generator DefaultLuceneDocumentGenerator \
  -threads 8 -input json_collection -index indexes/msmarco-passage-filtered -storePositions -storeDocvectors -storeRaw

2024-08-29 18:25:07,691 INFO  [main] index.IndexCollection (IndexCollection.java:631) - Setting log level to INFO
2024-08-29 18:25:07,713 INFO  [main] index.IndexCollection (IndexCollection.java:634) - Starting indexer...
2024-08-29 18:25:07,713 INFO  [main] index.IndexCollection (IndexCollection.java:635) - ============ Loading Parameters ============
2024-08-29 18:25:07,714 INFO  [main] index.IndexCollection (IndexCollection.java:636) - DocumentCollection path: json_collection
2024-08-29 18:25:07,715 INFO  [main] index.IndexCollection (IndexCollection.java:637) - CollectionClass: JsonCollection
2024-08-29 18:25:07,717 INFO  [main] index.IndexCollection (IndexCollection.java:638) - Generator: DefaultLuceneDocumentGenerator
2024-08-29 18:25:07,719 INFO  [main] index.IndexCollection (IndexCollection.java:639) - Threads: 8
2024-08-29 18:25:07,719 INFO  [main] index.IndexCollection (IndexCollection.java:640) - Stemmer: porter
2024-08-29 18:25:07,728 INFO  [main] index.IndexCollection (Ind

Example

In [ ]:
from pyserini.search import SimpleSearcher

# Initialize the searcher with the indexed data
searcher = SimpleSearcher('indexes/msmarco-passage-filtered')

# Create a mapping from query_id to passage_text
query_to_passage_mapping = {
    str(item['doc_id']): item['passage_text'] for item in train_data}


# Sample input query
sample_query = "What is the capital of France?"

# Perform the search
# k is the number of top results to return
hits = searcher.search(sample_query, k=10)

# Print the search results
print("Search results for the query:", sample_query)
for i, hit in enumerate(hits):
    passage = query_to_passage_mapping.get(hit.docid, "Passage not found")
    print(
        f"Rank: {i+1}, DocID: {hit.docid}, Passage: {passage}, Score: {hit.score:.4f}")


Search results for the query: What is the capital of France?
Rank: 1, DocID: 1375804, Passage: 1 Quebec is the capital and Montreal the largest city.  also Quebec City or QuÃ©bec City The capital of Quebec, Canada, in the southern part of the province on the St. Lawrence River. Founded in 1608 by Samuel de Champlain, it served as capital of New France before becoming a provincial capital under the British., Score: 7.0165
Rank: 2, DocID: 6214425, Passage: St. Denis (aka St. Denys) is the patron of France, where he preached the Gospel, and in whose capital city he suffered martyrdom. Denis (or Denys) was born and raised in Italy. Pope St. Clement sent Denys as a missionary to France., Score: 6.6756
Rank: 3, DocID: 2958538, Passage: Avignon, city, capital of Vaucluse dÃ©partement, Provence-Alpes-CÃ´te dâAzur rÃ©gion, southeastern France. It lies at a point on the east bank of the RhÃ´ne River where the narrow valley opens into a broad delta plain, northwest of NÃ®mes. It was the capital

In [ ]:

def run_all_queries(file, topics, searcher):
    with open(file, 'w') as runfile:
        cnt = 0
        print('Running {} queries in total'.format(len(topics)))
        for item in topics:
            query_id = item['query_id']
            query_text = item['pseudo_query_text']

            hits = searcher.search(query_text, 1000)
            seen_docs = set()
            for i in range(len(hits)):
                doc_id = hits[i].docid
                if doc_id not in seen_docs:
                    seen_docs.add(doc_id)
                    _ = runfile.write('{} Q0 {} {} {:.6f} Anserini\n'.format(
                        query_id, doc_id, i+1, hits[i].score))
            cnt += 1
            if cnt % 100 == 0:
                print(f'{cnt} queries completed')


# Load eval data
with open(test_data_path, 'r') as f:
    test_data = json.load(f)

# Run all queries and create the run file
run_all_queries('run-msmarco-passage-bm25.txt', test_data, searcher)


Running 18000 queries in total
100 queries completed
200 queries completed
300 queries completed
400 queries completed
500 queries completed
600 queries completed
700 queries completed
800 queries completed
900 queries completed
1000 queries completed
1100 queries completed
1200 queries completed
1300 queries completed
1400 queries completed
1500 queries completed
1600 queries completed
1700 queries completed
1800 queries completed
1900 queries completed
2000 queries completed
2100 queries completed
2200 queries completed
2300 queries completed
2400 queries completed
2500 queries completed
2600 queries completed
2700 queries completed
2800 queries completed
2900 queries completed
3000 queries completed
3100 queries completed
3200 queries completed
3300 queries completed
3400 queries completed
3500 queries completed
3600 queries completed
3700 queries completed
3800 queries completed
3900 queries completed
4000 queries completed
4100 queries completed
4200 queries completed
4300 queries

Create a qrels file for evaluation of the dataset, as required by pyserini:

In [ ]:

# Create a qrels file for the evaluation data, ensuring no duplicates
seen_pairs = set()
with open('collections/msmarco-passage/custom_qrels.tsv', 'w') as f:
    for item in test_data:
        query_id = item['query_id']
        doc_id = item['doc_id']
        relevance = 1  # Assuming all pairs in eval_data are relevant
        if (query_id, doc_id) not in seen_pairs:
            f.write(f'{query_id} 0 {doc_id} {relevance}\n')
            seen_pairs.add((query_id, doc_id))


In [ ]:
!python -m pyserini.eval.trec_eval -c -mmap -m P.3 -m set_P -m set_map collections/msmarco-passage/custom_qrels.tsv run-msmarco-passage-bm25.txt

jtreceval-0.0.5-jar-with-dependencies.jar: 1.79MB [00:00, 3.51MB/s]                
Running command: ['java', '-jar', '/root/.cache/pyserini/eval/jtreceval-0.0.5-jar-with-dependencies.jar', '-c', '-mmap', '-m', 'P.3', '-m', 'set_P', '-m', 'set_map', 'collections/msmarco-passage/custom_qrels.tsv', 'run-msmarco-passage-bm25.txt']
Results:
map                   	all	0.6954
P_3                   	all	0.2543
set_P                 	all	0.0012
set_map               	all	0.0012



In [ ]:
#!python -m pyserini.eval.trec_eval -c -mrecall.1000 -mmap -M1000 -m P.10 -m P.20 -m P.30 -m recip_rank collections/msmarco-passage/custom_qrels.tsv run-msmarco-passage-bm25.txt


# Dataset manager

In [ ]:
import torch

device = torch.device( 'cuda' if torch.cuda.is_available() else 'cpu' )

In [ ]:
from pytorch_lightning.loggers import TensorBoardLogger

# Set up TensorBoard logger
log_dir = "tb_logs"
# name="cluster_predictor")
logger = TensorBoardLogger(log_dir, name="combined_model")


In [ ]:
import json

from torch.utils.data import Dataset, DataLoader
from sentence_transformers import SentenceTransformer
import pytorch_lightning as pl
from transformers import AutoTokenizer, T5ForConditionalGeneration


class QueryPassageDataset(Dataset):
    def __init__(self, data, t5_model_name, sentence_model_name, max_input_length=512, max_target_length=128, mode='train'):
        self.data = data
        self.mode = mode
        self.tokenizer = SentenceTransformer(sentence_model_name)
        self.t5_tokenizer = AutoTokenizer.from_pretrained(t5_model_name)
        self.t5_model_name = t5_model_name
        self.max_input_length = max_input_length
        self.max_target_length = max_target_length

    def __len__(self):
        return len(self.data)

    def __getitem__(self, idx):
        item = self.data[idx]
        query_text = item['query_text'] if self.mode == 'train' else item['pseudo_query_text']
        passage_text = item['passage_text']
        query_id = item['query_id']
        doc_id = item['doc_id']
        cluster_id = item.get('cluster_id', -1)
        target = str(doc_id)  # Use the document ID as the target sequence

        tokenized_query = self.tokenizer.encode(
            query_text, convert_to_tensor=True)
        # tokenized_passage = self.tokenizer.encode(passage_text, convert_to_tensor=True)

        model_inputs = self.preprocess_data({
            'query_text': query_text,
            'target': target
        })

        return {
            'query_text': query_text,
            'tokenized_query': tokenized_query,
            'input_ids': model_inputs['input_ids'].clone().detach().squeeze(0),
            'attention_mask': model_inputs['attention_mask'].clone().detach().squeeze(0),
            'labels': model_inputs['labels'].clone().detach().squeeze(0),
            'cluster_id': cluster_id,
            'query_id': query_id,
            'doc_id': doc_id,
            'passage_text': passage_text
        }

    def preprocess_data(self, examples):
        inputs = examples["query_text"]
        targets = examples["target"]

        # Tokenize the inputs and targets
        model_inputs = self.t5_tokenizer(
            inputs, max_length=self.max_input_length, truncation=True, padding='max_length', return_tensors='pt')
        labels = self.t5_tokenizer(targets, max_length=self.max_target_length,
                                   truncation=True, padding='max_length', return_tensors='pt')

        model_inputs["labels"] = labels["input_ids"]
        return model_inputs

    def decode_tokenized_text(self, token_ids):
        return self.t5_tokenizer.decode(token_ids, skip_special_tokens=True)


class QueryPassageDataModule(pl.LightningDataModule):
    def __init__(self, train_data, test_data, eval_data, t5_model_name, sentence_model_name='all-MiniLM-L6-v2', batch_size=16):
        super().__init__()
        self.train_data = train_data
        self.test_data = test_data
        self.eval_data = eval_data
        self.sentence_model_name = sentence_model_name
        self.batch_size = batch_size
        self.t5_model_name = t5_model_name

    def setup(self, stage=None):
        self.train_dataset = QueryPassageDataset(
            self.train_data, self.t5_model_name, self.sentence_model_name, mode='train')
        self.test_dataset = QueryPassageDataset(
            self.test_data, self.t5_model_name, self.sentence_model_name, mode='test')
        self.eval_dataset = QueryPassageDataset(
            self.eval_data, self.t5_model_name, self.sentence_model_name, mode='eval')

    def train_dataloader(self):
        return DataLoader(self.train_dataset, batch_size=self.batch_size, shuffle=True, collate_fn=self.custom_collate_fn)

    def test_dataloader(self):
        return DataLoader(self.test_dataset, batch_size=self.batch_size, shuffle=False, collate_fn=self.custom_collate_fn)

    def val_dataloader(self):
        return DataLoader(self.eval_dataset, batch_size=self.batch_size, shuffle=False, collate_fn=self.custom_collate_fn)

    def custom_collate_fn(self, batch):
        # Handle the tensors separately
        # input_ids = torch.nn.utils.rnn.pad_sequence([item['input_ids'] for item in batch], batch_first=True, padding_value=self.t5_tokenizer.pad_token_id)
        # attention_mask = torch.nn.utils.rnn.pad_sequence([item['attention_mask'] for item in batch], batch_first=True, padding_value=0)

        input_ids = torch.nn.utils.rnn.pad_sequence(
            [item['input_ids'] for item in batch], batch_first=True, padding_value=0)
        attention_mask = torch.nn.utils.rnn.pad_sequence(
            [item['attention_mask'] for item in batch], batch_first=True, padding_value=0)


        labels = torch.stack([item['labels'] for item in batch])

        # Handle the non-tensor elements separately
        non_tensor_keys = ['query_text', 'tokenized_query',
                           'query_id', 'doc_id', 'passage_text']
        non_tensor_elements = {key: [item[key]
                                     for item in batch] for key in non_tensor_keys}

        non_tensor_elements['tokenized_query'] = torch.stack(
            non_tensor_elements['tokenized_query'])

        # Convert cluster_id list to a tensor
        cluster_ids = torch.tensor([item['cluster_id'] for item in batch])

        # Combine tensor and non-tensor elements into a single batch
        batch = {
            'input_ids': input_ids,
            'attention_mask': attention_mask,
            'labels': labels,
            'cluster_id': cluster_ids,
            **non_tensor_elements
        }

        return batch


## Some small test

In [ ]:
# Paths to the JSON files
train_data_path = 'collections/msmarco-passage/train_data_with_passages_ids.json'
test_data_path = 'collections/msmarco-passage/test_data_with_passages_ids.json'
eval_data_path = 'collections/msmarco-passage/eval_data_with_passages_ids.json'

# Load the datasets
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(test_data_path, 'r') as f:
    test_data = json.load(f)

with open(eval_data_path, 'r') as f:
    eval_data = json.load(f)

# Prepare data
data_module = QueryPassageDataModule(train_data, test_data, eval_data,
                                     sentence_model_name='all-MiniLM-L6-v2', t5_model_name='t5-small', batch_size=16)


In [ ]:
# Check the data loading
train_loader = data_module.setup()
train_loader = data_module.train_dataloader()

it = iter(train_loader)
first = next(it)
print(first['tokenized_query'])


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/349 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/10.7k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/2.32k [00:00<?, ?B/s]

spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.39M [00:00<?, ?B/s]

tensor([[ 0.0408, -0.0476,  0.0116,  ..., -0.0455, -0.0900,  0.0176],
        [ 0.0127,  0.0090,  0.0361,  ..., -0.0301, -0.0140, -0.0169],
        [ 0.0340, -0.0335, -0.0645,  ..., -0.0263,  0.1153,  0.0034],
        ...,
        [ 0.0309, -0.0285, -0.0311,  ..., -0.0532, -0.0197,  0.0114],
        [-0.0934,  0.0300, -0.0550,  ..., -0.0495,  0.0755, -0.0284],
        [ 0.0469, -0.0073, -0.0086,  ...,  0.0165, -0.0096, -0.0104]],
       device='cuda:0')


In [ ]:
first['attention_mask'][0]


tensor([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,

In [ ]:
first['query_text'][0]


'signs and symptoms of iodine deficiency'

In [ ]:
first['doc_id'][0]


3798005

In [ ]:
print(len(first['tokenized_query']))


16


In [ ]:
# Get the data type of the tensor
dtype = first['tokenized_query'][0].dtype

print(dtype)


torch.float32


In [ ]:
print(first['query_text'])


['signs and symptoms of iodine deficiency', 'where is elements of byron located', 'econofoods headquarters', 'is there a generic for ciprodex ear drops', 'what is flecainide for', 'what is the objective of bt maize', 'how much does uptodate subscription cost', 'header meaning', 'enchilada definition', 'cost of orthodontics for children', 'what county is carroll indiana in', 'what fabric does velcro stick to', 'what is the shabaka stone', 'how long for coconut oil to improve hair grow', 'can you grind hemp seeds', 'what are the three main components of total energy expenditure']


In [ ]:
print(len(first['query_text']))


16


In [ ]:
print(len(first['labels']))


16


# Model Architecture - Cluster Predictor

In [ ]:
import torch
import torch.nn as nn
from sentence_transformers import SentenceTransformer
import pytorch_lightning as pl


class ClusterPredictor(pl.LightningModule):
    def __init__(self, model_name='all-MiniLM-L6-v2', num_clusters=2000):
        super(ClusterPredictor, self).__init__()
        self.encoder = SentenceTransformer(model_name)
        self.linear = nn.Linear(
            self.encoder.get_sentence_embedding_dimension(), num_clusters)
        self.relu = nn.ReLU()
        self.loss_fn = nn.CrossEntropyLoss()

    def forward(self, tokenized_queries):
        logits = self.relu(self.linear(tokenized_queries))
        return logits

    def training_step(self, batch, batch_idx):
        tokenized_queries = batch['tokenized_query']
        cluster_ids = batch['cluster_id']
        logits = self(tokenized_queries)

        loss = self.loss_fn(logits, cluster_ids)
        self.log('train_loss', loss, on_step=True,
                 on_epoch=True, prog_bar=True, logger=True)
        return loss

    def validation_step(self, batch, batch_idx):
        tokenized_queries = batch['tokenized_query']
        cluster_ids = batch['cluster_id']
        logits = self(tokenized_queries)
        loss = self.loss_fn(logits, cluster_ids)
        self.log('val_loss', loss, on_step=True,
                 on_epoch=True, prog_bar=True, logger=True)
        return loss

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=1e-2)


## Train cluster predictor model (Not needed anymore, weights already saved and can be loaded)

In [ ]:
# Paths to the JSON files
train_data_path = 'collections/msmarco-passage/train_data_with_passages_ids.json'
test_data_path = 'collections/msmarco-passage/test_data_with_passages_ids.json'
eval_data_path = 'collections/msmarco-passage/eval_data_with_passages_ids.json'

# Load the datasets
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(test_data_path, 'r') as f:
    test_data = json.load(f)

with open(eval_data_path, 'r') as f:
    eval_data = json.load(f)

# Prepare data
data_module = QueryPassageDataModule(train_data, test_data, eval_data,
                                     sentence_model_name='all-MiniLM-L6-v2', t5_model_name='t5-small', batch_size=2048)


In [ ]:


# Initialize and train the ClusterPredictor
cluster_predictor = ClusterPredictor(num_clusters=2000)
trainer = pl.Trainer(max_epochs=3, accelerator="auto",
                     logger=logger, log_every_n_steps=5)
trainer.fit(cluster_predictor, data_module)


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name    | Type                | Params | Mode 
--------------------------------------------------------
0 | encoder | SentenceTransformer | 22.7 M | train
1 | linear  | Linear              | 770 K  | train
2 | relu    | ReLU                | 0      | train
3 | loss_fn | CrossEntropyLoss    | 0      | train
--------------------------------------------------------
23.5 M    Trainable params
0         Non-trainable params
23.5 M    Total params
93.933    Total estimated model params size (MB)
7         Modules in train mode
120       Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/pytorch_lightning/utilities/data.py:78: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 2000. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.


Training: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/pytorch_lightning/utilities/data.py:78: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 2048. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.
INFO:pytorch_lightning.utilities.rank_zero:
Detected KeyboardInterrupt, attempting graceful shutdown ...


NameError: name 'exit' is not defined

In [ ]:
# Load the TensorBoard notebook extension
%load_ext tensorboard

# Launch TensorBoard
%tensorboard - -logdir tb_logs


In [ ]:
# Save the model weights after training
#torch.save(cluster_predictor.state_dict(), 'cluster_prediector_weights.pth')


In [ ]:
#!tar - czvf tb_logs.tar.gz tb_logs


In [ ]:
import numpy as np
from tqdm import tqdm

# Accuracy evaluation
def evaluate_cluster_predictor(model, eval_loader):
    model#.to('cuda')
    model.eval()
    all_preds = []
    all_labels = []

    with torch.no_grad():
        for batch in tqdm(eval_loader, desc="Evaluating"):
            tokenized_query_texts, _, _, cluster_ids, _ = batch
            logits = model(tokenized_query_texts)#.to('cuda'))
            preds = torch.argmax(logits, dim=1)
            all_preds.extend(preds.cpu().numpy())
            all_labels.extend(cluster_ids.cpu().numpy())

    # Convert to numpy arrays for easier metric computation
    all_preds = np.array(all_preds)
    all_labels = np.array(all_labels)

    # Calculate metrics
    accuracy = np.mean(all_preds == all_labels)
    print(f'Cluster Prediction Accuracy: {accuracy:.4f}')


eval_loader = data_module.test_dataloader()
# Evaluate the trained model
evaluate_cluster_predictor(cluster_predictor, eval_loader)


# Model Architecture - refinement model & combined model

In [ ]:
from transformers import AutoModelForSeq2SeqLM


class Seq2SeqRefinementModel(pl.LightningModule):
    def __init__(self, model_name='t5-small'):
        super(Seq2SeqRefinementModel, self).__init__()
        self.tokenizer = AutoTokenizer.from_pretrained(model_name)
        # T5ForConditionalGeneration.from_pretrained(model_name)
        self.model = AutoModelForSeq2SeqLM.from_pretrained(model_name)
        self.loss_fn = nn.CrossEntropyLoss()
        self.cluster_embedding_dim = 2000
        self.input_embedding_dim = self.model.config.d_model

        # Linear layer to project cluster embeddings to input embedding size
        self.projection_layer = nn.Linear(
            self.cluster_embedding_dim, self.input_embedding_dim)

    def forward(self, input_ids, attention_mask, cluster_logits, labels=None):

        # Step 2: Embed the query using T5 model

        t5_encoder_outputs = self.model.encoder(
            input_ids=input_ids, attention_mask=attention_mask)
        # (batch_size, seq_length, hidden_dim)
        query_embeddings = t5_encoder_outputs.last_hidden_state

        # Sum the embeddings
        # cluster_embeddings_expanded = cluster_logits.unsqueeze(1).expand(-1, query_embeddings.size(1), -1)

        cluster_embeddings_projection = self.projection_layer(cluster_logits)
        # Expand cluster_embeddings to match the shape of query_embeddings
        # cluster_embeddings_expanded = cluster_embeddings_projection.unsqueeze(1).expand(-1, query_embeddings.size(1), -1)  # Shape: [batch_size, seq_length, hidden_dim]

        combined_embeddings = query_embeddings + \
            cluster_embeddings_projection.unsqueeze(1)

        # Pass the combined embeddings through the T5 model

        outputs = self.model(
            inputs_embeds=combined_embeddings,
            attention_mask=attention_mask,
            labels=labels
        )

        loss = outputs.loss
        logits = outputs.logits

        return loss, logits

    # JUST FOR DEBBUG
    # def training_step(self, batch, batch_idx):
    #    input_ids, cluster_embeddings, target_ids = batch['input_ids'], torch.randn(16,328), batch['labels']
    #    loss, _ = self(input_ids, cluster_embeddings, target_ids)
    #    self.log('train_loss', loss)
    #    return loss

    # def configure_optimizers(self):
    #    return torch.optim.AdamW(self.parameters(), lr=5e-5)


In [ ]:
# ONLY FOR DEBUG
# Initialize the model
# model = Seq2SeqRefinementModel()

# Test the model with PyTorch Lightning
# trainer = pl.Trainer(max_epochs=1, accelerator="auto")
# trainer.fit(model, data_module)


In [ ]:
class CombinedModel(pl.LightningModule):
    def __init__(self, cluster_predictor, refinement_model, learning_rate=2e-5):
        super(CombinedModel, self).__init__()
        self.cluster_predictor = cluster_predictor
        self.refinement_model = refinement_model
        self.learning_rate = learning_rate

        # Freeze cluster_predictor
        for param in self.cluster_predictor.parameters():
            param.requires_grad = False

    def training_step(self, batch, batch_idx):
        # Step 1: Get cluster prediction logits
        tokenized_queries = batch['tokenized_query']
        input_ids, attention_mask, t5_tokenized_target = batch[
            'input_ids'], batch['attention_mask'], batch['labels']

        cluster_logits = self.cluster_predictor(tokenized_queries)

        # Forward pass through Seq2Seq Refinement Model
        loss, logits = self.refinement_model(
            input_ids=input_ids,
            attention_mask=attention_mask,
            cluster_logits=cluster_logits,
            labels=t5_tokenized_target
        )

        # Compute loss
        self.log('train_loss', loss, on_step=True,
                 on_epoch=True, prog_bar=True, logger=True)
        return loss

    def validation_step(self, batch, batch_idx):
        # Step 1: Get cluster prediction logits
        tokenized_queries = batch['tokenized_query']
        input_ids, attention_mask, t5_tokenized_target = batch[
            'input_ids'], batch['attention_mask'], batch['labels']

        cluster_logits = self.cluster_predictor(tokenized_queries)

        # Forward pass through Seq2Seq Refinement Model
        loss, logits = self.refinement_model(
            input_ids=input_ids,
            attention_mask=attention_mask,
            cluster_logits=cluster_logits,
            labels=t5_tokenized_target
        )
        # Compute loss
        self.log('val_loss', loss, on_step=True,
                 on_epoch=True, prog_bar=True, logger=True)
        return loss

    def generate(self, tokenized_queries, input_ids, attention_mask, num_beams=5, top_k=3, max_length=50):
        # Step 1: Get cluster prediction logits
        cluster_logits = self.cluster_predictor(tokenized_queries)

        # Project cluster logits to match the input embedding dimension
        cluster_embeddings_projection = self.refinement_model.projection_layer(
            cluster_logits)

        combined_embeddings = self.refinement_model.model.encoder(
            input_ids=input_ids, attention_mask=attention_mask
        ).last_hidden_state + cluster_embeddings_projection.unsqueeze(1)

        # Generate sequences using the combined embeddings with beam search
        generated_outputs = self.refinement_model.model.generate(
            inputs_embeds=combined_embeddings,
            attention_mask=attention_mask,
            max_length=max_length,
            num_beams=num_beams,  # Beam search to improve generation
            num_return_sequences=top_k,  # Return the top_k sequences
            output_scores=True,  # Return the scores associated with each sequence
            return_dict_in_generate=True  # Return a structured dictionary with all outputs
        )

        # Extract the sequences and their scores
        generated_ids = generated_outputs.sequences  # The generated sequences
        # The log probabilities of each sequence
        scores = generated_outputs.sequences_scores

        return generated_ids, scores

    def configure_optimizers(self):
        return torch.optim.Adam(self.parameters(), lr=self.learning_rate)


In [ ]:
# Paths to the JSON files
train_data_path = 'collections/msmarco-passage/train_data_with_passages_ids.json'
test_data_path = 'collections/msmarco-passage/test_data_with_passages_ids.json'
eval_data_path = 'collections/msmarco-passage/eval_data_with_passages_ids.json'

# Load the datasets
with open(train_data_path, 'r') as f:
    train_data = json.load(f)

with open(test_data_path, 'r') as f:
    test_data = json.load(f)

with open(eval_data_path, 'r') as f:
    eval_data = json.load(f)

# Prepare data
data_module = QueryPassageDataModule(train_data, test_data, eval_data,
                                     sentence_model_name='all-MiniLM-L6-v2', t5_model_name='t5-small', batch_size=16)


In [ ]:
# Initialize models
cluster_predictor = ClusterPredictor()
# Load the saved model weights
cluster_predictor.load_state_dict(torch.load('cluster_predictor_weights.pth'))

refinement_model = Seq2SeqRefinementModel()

# Initialize combined model
combined_model = CombinedModel(cluster_predictor, refinement_model)
combined_model.load_state_dict(torch.load('combined_model.pth'))


<ipython-input-49-4b1faa9fe377>:4: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  cluster_predictor.load_state_dict(torch.load('cluster_predictor_weights.pth'))
<ipython-inpu

<All keys matched successfully>

## Train combined model

In [ ]:
# Train the combined model
trainer = pl.Trainer(max_epochs=1, accelerator="auto",
                     logger=logger, log_every_n_steps=5)
trainer.fit(combined_model, data_module)


INFO:pytorch_lightning.utilities.rank_zero:GPU available: True (cuda), used: True
INFO:pytorch_lightning.utilities.rank_zero:TPU available: False, using: 0 TPU cores
INFO:pytorch_lightning.utilities.rank_zero:HPU available: False, using: 0 HPUs
INFO:pytorch_lightning.accelerators.cuda:LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
INFO:pytorch_lightning.callbacks.model_summary:
  | Name              | Type                   | Params | Mode 
---------------------------------------------------------------------
0 | cluster_predictor | ClusterPredictor       | 23.5 M | train
1 | refinement_model  | Seq2SeqRefinementModel | 61.5 M | train
---------------------------------------------------------------------
61.5 M    Trainable params
23.5 M    Non-trainable params
85.0 M    Total params
340.057   Total estimated model params size (MB)
11        Modules in train mode
397       Modules in eval mode


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/pytorch_lightning/utilities/data.py:78: Trying to infer the `batch_size` from an ambiguous collection. The batch size we found is 16. To avoid any miscalculations, use `self.log(..., batch_size=batch_size)`.


Training: |          | 0/? [00:00<?, ?it/s]

INFO:pytorch_lightning.utilities.rank_zero:
Detected KeyboardInterrupt, attempting graceful shutdown ...


NameError: name 'exit' is not defined

In [ ]:
# Save the model weights after training
# torch.save(combined_model.state_dict(), 'combined_model_1.pth')


## Evaluation combined model
TO do that, we need to use the same function for evaluation that we used with pyserini. So we need to create corresponding files

In [ ]:
import torch


def predict_combined_model(combined_model, dataloader, top_k=3):
    combined_model.to(device).eval()  # Set the model to evaluation mode
    results = []

    with torch.no_grad():  # Disable gradient calculation for evaluation
        for batch in dataloader:
            tokenized_queries = batch['tokenized_query'].to(device)# .to("cpu")
            input_ids = batch['input_ids'].to(device)#.to("cuda")  # .to("cuda")
            attention_mask = batch['attention_mask'].to(device)#.to("cuda")  # .to("cpu")

            # Generate top-k document IDs and their associated scores
            generated_ids, scores = combined_model.generate(
                tokenized_queries, input_ids, attention_mask, num_beams=top_k, top_k=top_k
            )

            # Decode the generated sequences to get document IDs
            top_doc_ids = [combined_model.refinement_model.tokenizer.decode(
                g, skip_special_tokens=True) for g in generated_ids]

            for i in range(len(batch['query_id'])):
                query_id = batch['query_id'][i]
                for j in range(top_k):
                    results.append({
                        'query_id': query_id,
                        'doc_id': top_doc_ids[i * top_k + j],
                        # Convert score to a Python scalar
                        'score': scores[i * top_k + j].item()
                    })

    return results


data_module.setup()
test_dataloader = data_module.test_dataloader()  # Use the test dataloader


results = predict_combined_model(combined_model, test_dataloader)
# Print the predicted doc_id along the query id and score
print(results)


[{'query_id': 80001, 'doc_id': '676767', 'score': -2.784696340560913}, {'query_id': 80001, 'doc_id': '676769', 'score': -2.8230509757995605}, {'query_id': 80001, 'doc_id': '676768', 'score': -2.8274855613708496}, {'query_id': 80002, 'doc_id': '636363', 'score': -2.7317311763763428}, {'query_id': 80002, 'doc_id': '639494', 'score': -2.7487165927886963}, {'query_id': 80002, 'doc_id': '636394', 'score': -2.786431312561035}, {'query_id': 80003, 'doc_id': '636363', 'score': -2.742196559906006}, {'query_id': 80003, 'doc_id': '639494', 'score': -2.8121981620788574}, {'query_id': 80003, 'doc_id': '636369', 'score': -2.8202667236328125}, {'query_id': 80005, 'doc_id': '696969', 'score': -2.754595994949341}, {'query_id': 80005, 'doc_id': '676969', 'score': -2.7831406593322754}, {'query_id': 80005, 'doc_id': '6767691', 'score': -2.846247434616089}, {'query_id': 80006, 'doc_id': '676767', 'score': -2.714771032333374}, {'query_id': 80006, 'doc_id': '676969', 'score': -2.728699207305908}, {'query_id'

In [ ]:
def save_results_trec_format(results, output_file='run-results.txt'):
    with open(output_file, 'w') as f:
        for i, result in enumerate(results):
            query_id = result['query_id']
            doc_id = result['doc_id']
            score = result['score']
            rank = i + 1  # Rank is based on the order in which results are written
            f.write(f'{query_id} Q0 {doc_id} {rank} {score:.6f} CombinedModel\n')


# Save the results in TREC format
save_results_trec_format(results, 'run-results.txt')


In [ ]:

# Initialize an empty set to track seen (query_id, doc_id) pairs
seen_pairs = set()

# Open a file to write the Qrels data
with open('collections/msmarco-passage/custom_qrels_test.tsv', 'w') as f:
    for batch in test_dataloader:
        query_ids = batch['query_id']
        doc_ids = batch['doc_id']

        for query_id, doc_id in zip(query_ids, doc_ids):
            relevance = 1  # Assuming all pairs in test_data are relevant

            # Check if the (query_id, doc_id) pair has already been seen
            if (query_id, doc_id) not in seen_pairs:
                # Write the pair to the Qrels file
                f.write(f'{query_id} 0 {doc_id} {relevance}\n')
                # Add the pair to the seen set to avoid duplicates
                seen_pairs.add((query_id, doc_id))


In [ ]:
!python -m pyserini.eval.trec_eval -c -mmap -m P.3 -m set_P -m set_map collections/msmarco-passage/custom_qrels_test.tsv run-results.txt


/root/.cache/pyserini/eval/jtreceval-0.0.5-jar-with-dependencies.jar already exists!
Skipping download.
Running command: ['java', '-jar', '/root/.cache/pyserini/eval/jtreceval-0.0.5-jar-with-dependencies.jar', '-c', '-mmap', '-m', 'P.3', '-m', 'set_P', '-m', 'set_map', 'collections/msmarco-passage/custom_qrels_test.tsv', 'run-results.txt']
Results:
map                   	all	0.0000
P_3                   	all	0.0000
set_P                 	all	0.0000
set_map               	all	0.0000

